# [Digit Factorial Chains](https://projecteuler.net/problem=74)

We previously looked at the sum of digit factorials in [problem 34](https://projecteuler.net/problem=34). This time's a little different, since we're *repeatedly* summing digit factorials to find cycles. We can reuse our function implementation from that problem, though.

In [1]:
from functools import cache

@cache
def sfd(n):
    q = n // 10
    if q == 0:
        return factorial(n)
    
    return factorial(n % 10) + sfd(q)

A natural way to find the chain lengths is with a memoized recursive function, since we know every starting value will eventually reach one of these cases.

In [2]:
@cache
def chain_length(n):
    if n in {1, 2, 145, 40585}:
        return 1
    elif n in {169, 363601, 1454}:
        return 3
    elif n in {871, 45361, 872, 45362}:
        return 2
    
    return 1 + chain_length(sfd(n))

Then we just iterate through every starting value below 1000000.

In [3]:
long_chains = []
for n in range(0, 1000000):
    if chain_length(n) == 60:
        long_chains.append(n)
              
len(long_chains)

402

This is decently fast, but with some clever combinatorics, we can get the answer even quicker.

## Multisets and multinomials

Suppose a number $n$ is composed solely of digits 1-9 (we'll get to including 0 in a bit). Every permutation of those digits will have the same digit factorial sum as $n$, and therefore the same chain length. This means we only have to check each multiset of digits 1-9 once, and if the chain length is 60, we'll count every distinct permutation of those digits using the multinomial coefficient. (See [problem 92](https://projecteuler.net/problem=92) for a little more explanation of these concepts.)

There are quirks with handling 0 here. Since $0! = 1$, it might seem that we can replace any instance of 1 in a number with 0 and get another number with the same chain length. However, this fails to handle the case that 1 is the first digit. When that happens, since the 0 is now a leading 0, we don't include it in the sum of digit factorials calculation, which changes the chain length. For example, the number 1218 has a digit factorial sum of 40324, as does 1208, but 0218 is just 218, and its digit factorial sum is 40323.

For that reason, if we simply count the multinomial coefficient twice for every number with 1 as a digit, we'll overcount. Fortunately, we can correct for this using the [inclusion-exclusion principle](https://en.wikipedia.org/wiki/Inclusion%E2%80%93exclusion_principle).

Counting with combinatorics reduces the search space significantly - from a million numbers to check to only thousands. We also end up finding that there aren't that many combinations of digits that result in a chain length of 60.

In [4]:
from itertools import combinations_with_replacement

cs = set()
for i in range(1, 7):
    for digits in combinations_with_replacement(range(1, 10), i):
        n = sum(10^k * d for (k, d) in enumerate(reversed(digits)))
        if chain_length(n) == 60:
            cs.add(digits)
            
cs

{(1, 4, 7, 9), (2, 2, 3, 4, 7, 9)}

As explained above, any permutation of these two multisets of digits will result in a number with a chain length of 60. Additionally, if we replace 1 in `(1, 4, 7, 9)` with 0, any permutation where 0 is not the most significant digit will also have a chain length of 60.

You could just work this by hand at this point:
$$\frac{4!}{(1!)(1!)(1!)(1!)} + 3 \times \frac{3!}{(1!)(1!)(1!)} + \frac{6!}{(2!)(1!)(1!)(1!)(1!)(1!)} = 402$$
Or we could have the computer count for us.

In [5]:
from collections import Counter
from itertools import count

def include_exclude(multiset):
    total = 0
    for i in count(0):
        total += (-1)^i * multinomial(multiset.values())
        multiset[1] -= 1
        if multiset[1] == 0:
            del multiset[1]
            total += (-1)^(i+1) * multinomial(multiset.values())
            break
    
    return total


def sfd_permutations(digits):
    multiset = Counter(digits)
    total = multinomial(multiset.values())

    if multiset[1] >= 1:
        total += include_exclude(multiset)
        
    return total


sum(sfd_permutations(digits) for digits in cs)

402

## Relevant sequences
* Numbers that eventually cycle when summing digit factorials: [A188284](https://oeis.org/A188284)
* Digit factorial chain lengths: [A303935](https://oeis.org/A303935)